<a href="https://colab.research.google.com/github/tluxxx/vbt_basics/blob/main/vbt_test_05.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction into vectorbt - part 5
* valid for latest free version (version: 0.28.1)
* multi-ticker portfolio

Content:

* download data for multi-ticker-portfolio and preprocessing
* generating signals by SMA/RSI-strategy
* baseline multi-ticker portfolio and standard outputs
* advanced use of `Portfolio`-object for multi tickers:
    * distributed initial cash
    * cash-pooling (with and without order size limitations)
    * groups of tickers, group-cash-pool (with and without order size-limitations)
    * Long/Short strategies

In [1]:
!pip install vectorbt ta python-dotenv --quiet

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 420.7/420.7 kB 9.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 315.5/315.5 kB 21.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 42.8 MB/s eta 0:00:00


In [2]:
import vectorbt as vbt
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import yfinance as yf
import ta

## 0. Helpers

In [3]:
# connecting Google-Drive and importing function form helper-module
import sys
import importlib
import os
import helper

from google.colab import drive
from dotenv import load_dotenv

# connnecting Google-Drive, loading .env-file and getting path_data
from pathlib import Path
drive.mount('/content/drive')
load_dotenv('/content/drive/My Drive/.env')
path_data = os.getenv('PATH_VBT')           # replace it with your path
sys.path.append(path_data)

# importing supporting functions (from helper-module in path_data)
for mod in ['timelines', 'entries_exits', 'plotting_support']:
    importlib.reload(importlib.import_module(f'helper.{mod}'))

from helper.timelines import get_timeline_basic, get_timeline_extended
from helper.entries_exits import lense_at_entry_exit, classify_exit_types
from helper.plotting_support import (_is_boolean_series, plot_multi_subplot_trading_data,
                                     plot_signals_and_positions, plot_portfolio_positions,
                                     build_position_timeline, plot_positions_stacked)



Mounted at /content/drive


In [4]:
def results_multi_ticker(pf, init_cash_per_group=None):
    # Profits and trade count per ticker
    trades = pf.trades.records_readable

    stats_ticker = trades.groupby('Column').agg(
        Total_PnL=('PnL', 'sum'),
        Trade_Count=('PnL', 'count')
    )

    # Display per-ticker stats
    pd.options.display.float_format = '{:,.2f}'.format
    display(stats_ticker)

    # Calculate and print totals
    total_pnl = stats_ticker['Total_PnL'].sum()
    total_trades = stats_ticker['Trade_Count'].sum()
    print()
    print(f"Total Profit Across All Tickers: {total_pnl:,.3f}")
    print(f"Total Number of Trades: {total_trades}")

    # final portfolio value per group and return
    if init_cash_per_group is not None:
        final_group_value = pf.value().iloc[-1]
        group_pnl = (final_group_value - init_cash_per_group) / init_cash_per_group
        print()
        print('*** total return per Group *****')
        print(group_pnl.map('{:,.3f}'.format))

## 1. Data Download

For a multi-ticker portfolio, we first need to retrieve historical price data for all selected assets. As in the previous sections, we rely on the standard `yfinance` functionality to download the data. From the retrieved dataset, we extract the individual OHLC (Open, High, Low, Close) components.

Each price component is stored in its own DataFrame, using the date as the index and the corresponding ticker symbols as column names. This structure allows for clean, consistent handling of multiple assets and simplifies subsequent analysis.

In [5]:
# download OHLC-data
tickers = ['PFE', 'GOOG', 'MSFT', 'MRNA']
start_date = '2022-01-01'
end_date = '2025-10-11'
prices = yf.download(tickers, start=start_date, end=end_date, auto_adjust=True)

open = prices.Open
high = prices.High
low = prices.Low
close = prices.Close

[*********************100%***********************]  4 of 4 completed


We have choosen four tickers from two different market segements (Tech and Pharma) that shows very different behaviours. As an example may serve the value-development.

In [82]:
# trend visualisation
fig = go.Figure()

for ticker in tickers:
    normalized_close = (close[ticker] / close[ticker].iloc[0])
    fig.add_trace(go.Scatter(x=normalized_close.index, y=normalized_close, mode='lines', name=ticker))

fig.update_layout(title='Normalized Stock Price Trends', xaxis_title='Date', yaxis_title='Normalized Price', width=1000, height=400)
fig.show()

## 2. The SMA/RSI-strategy and their signals
2. The SMA/RSI-strategy and their signals
We will show the power of a Portfolio-instance, generated by the class-method `from_signals(...)` by implementing a strategy, that will deliver a large number of signals.

Entry- and Exits Signals are generated based on different constellations of fast-SMA, slow-SMA and the RSI. The code snippet below is self explaining. We will call this SMA/RSI-Strategy.

Note: Our tasks is to demonstrate the behaviour of a vbt Portfolioinstance, rather than presenting a brilliant strategy. Again, nobody would seriously consider implementing this strategy for trading in real life, however, it serves well for demonstration.

In [7]:
# strategy parameter
window_fast = 10
window_slow = 50
window_rsi = 14

# calculation of indicators, required for the strategy
fast_sma = pd.DataFrame(index=close.index, columns=close.columns)
slow_sma = pd.DataFrame(index=close.index, columns=close.columns)
rsi = pd.DataFrame(index=close.index, columns=close.columns)

for ticker in tickers:
    fast_sma[ticker] = ta.trend.sma_indicator(close[ticker], window=window_fast, fillna=False)
    slow_sma[ticker] = ta.trend.sma_indicator(close[ticker], window=window_slow, fillna=False)
    rsi[ticker] = ta.momentum.rsi(close[ticker], window=14, fillna=False)

# generation of signals
long_entries  = (fast_sma > slow_sma) & (rsi > 30)
long_exits    = (fast_sma < slow_sma) | (rsi < 70)
short_entries = (fast_sma < slow_sma) & (rsi < 70)
short_exits   = (fast_sma > slow_sma) | (rsi > 30)

As a result, we obtain a separate DataFrame for each type of signal, with dates as the index and ticker symbols as the columns.

Let’s briefly recap the progression so far:

* In the previous sections, we started with a strategy based on SMA crossovers. This approach relied on sequential, alternating signals, meaning that an exit signal strictly followed an entry signal, and vice versa.

* We then implemented a mean-reversion strategy using Bollinger Band touches. This strategy was based on non-alternating signals, where multiple entry signals could occur before an exit (and vice versa).

Both of these strategies were event-driven: signals were generated only at the precise moment an event occurred (such as a crossing or a band touch).

In contrast, the signals we generate now are purely condition-based rather than event-based. As long as a given condition remains true, the same signal may be emitted over multiple consecutive bars. Moreover, it is possible to generate multiple signals within a single bar.

Handling and resolving these potentially overlapping or conflicting signals is delegated entirely to the Portfolio instance.

To illustrate this behavior, we begin by examining the total number of generated signals.It is evident, that we get a significant higher number of signals, compared to the previous strategies.

In [9]:
signal_dfs = {'long_entries': long_entries, 'long_exits': long_exits,
              'short_entries': short_entries, 'short_exits': short_exits}

# preparation and collection
results = {}

for name, df in signal_dfs.items():
    true_counts = df.sum(axis=0)                 # True = sum of booleans
    total_counts = df.shape[0]                   # Number of rows
    false_counts = total_counts - true_counts    # False = total - True

    # Store the counts as a DataFrame with MultiIndex columns
    results[name] = pd.DataFrame({
        (name, 'True'): true_counts,
        (name, 'False'): false_counts
    })

# consolidation and display
combined_counts = pd.concat(results.values(), axis=1)
combined_counts.columns = pd.MultiIndex.from_tuples(combined_counts.columns)
display(combined_counts)

long_entries       long_exits       short_entries       short_exits  \
               True False       True False          True False        True   
Ticker                                                                       
GOOG            573   374        865    82           324   623         912   
MRNA            293   654        901    46           605   342         836   
MSFT            524   423        841   106           374   573         917   
PFE             345   602        917    30           552   395         875   

              
       False  
Ticker        
GOOG      35  
MRNA     111  
MSFT      30  
PFE       72

As already mentioned, we observe many bars that generate more than one signal.

In some cases, multiple signals on the same bar are conflicting:  
* Long entry and long exit
* Short entry and short exit
* Long entry and short entry
* Long exit and short exit

In other cases, multiple signals on the same bar may actually reinforce a particular market direction:
* Long exit and short entry — supports taking a short position
* Short exit and long entry — supports taking a long position

This is not merely an academic consideration. When we examine the number of bars with multiple signals generated by our strategy, we find that such situations occur frequently. In the following sections, we will see how vectorbt handles these types of signal conflicts internally.

In [10]:
# Calculate mask for multiple signals at one bar
multi_signals = {
    'long_entry_exit': long_entries & long_exits,           # Long Entry & Long Exit - valid conflict
    'short_entry_exit': short_entries & short_exits,        # Short Entry & Short Exit - valid conflict
    'long_entry_short_entry': long_entries & short_entries, # Long Entry & Short Entry - valid conflict
    'long_exit_short_exit': long_exits & short_exits,       # Long Exit & Short Exit - valid conflict
    'long_entry_short_exit': long_entries & short_exits,    # Long Entry & Short Exit - support going Long
    'long_exit_short_entry': long_exits & short_entries,    # Long Exit & Short Entry - support going short
}

# Count multi_signals per ticker for each type and createn/display results-dataframe
multi_signals_counts = {name: mask.sum(axis=0) for name, mask in multi_signals.items()}
multi_signals_df = pd.DataFrame(multi_signals_counts)
print("Combined MultiSignal Counts:")
display(multi_signals_df)


Combined MultiSignal Counts:


long_entry_exit  short_entry_exit  long_entry_short_entry  \
Ticker                                                              
GOOG                504               307                       0   
MRNA                260               516                       0   
MSFT                431               360                       0   
PFE                 328               501                       0   

        long_exit_short_exit  long_entry_short_exit  long_exit_short_entry  
Ticker                                                                      
GOOG                     843                    573                    324  
MRNA                     803                    293                    605  
MSFT                     824                    524                    374  
PFE                      858                    345                    552

## 3. Baseline Portfolio

Lets start with a baseline-portfolio as reference:
* multi-ticker portfolio
* LongOnly
* each ticker gets the same inital-cash
* no cash-sharing (cash is kept separately for each ticker)

A multi-ticker portfolio-instance with the features above can be generated as follows:

In [93]:
# equal cash-distribution
total_cash = 40_000
init_cash_per_ticker = total_cash / len(tickers)

# generation of a baseline portfolio instance (multiple tickers)
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    #short_entries=short_entries,   # no short-entry
    #short_exits=short_exits,       # no short-exit
    init_cash=init_cash_per_ticker, # evenly distributed inital cash
    freq='D'                        # daily evaluation of metrics
)

What about the conflicts, mentioned above?

In a LongOnly portfolio, we have only one type of conflict: Getting LongEntry and LongExit at the same bar.
The behaviour is controlled by the parameter `upon_long_conflict`. By default it is set to 'Ignore', as result conflicting signals will be ignored.

Other Options are:
* 'Entry': when LongConflict, execute entry, ignore exit,
* 'Exit': when LongConflict, ingore entry, execute exit (be very risk adverse in times of confusion),
* 'Adjacent': when LongConflict, execute both as separate orders,
* 'Opposite': when LongConflict, execute the opposite to the current position

So we can implement a quite sophisticated handling of conflicting signals. We will come back to this in detail when touching Long-Short-multiple-ticker-portfolios.

Now lets review standard outputs for an multi-ticker portfolio.


### Outputs: List of trades and visualisation of trades

In [94]:
# show trades
display(pf.trades.records_readable.head(3))
display(pf.trades.records_readable.tail(3))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 92.60      2023-02-02           107.99        0.00   
1              1   GOOG 72.14      2023-05-11           116.03        0.00   
2              2   GOOG 57.35      2024-01-24           149.23        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees       PnL  Return Direction  \
0     2023-02-23           90.39       0.00 -1,629.60   -0.16      Long   
1     2023-07-20          118.64       0.00    188.32    0.02      Long   
2     2024-02-27          139.06       0.00   -583.48   -0.07      Long   

   Status  Position Id  
0  Closed            0  
1  Closed            1  
2  Closed            2

Exit Trade Id Column   Size Entry Timestamp  Avg Entry Price  Entry Fees  \
18             18    PFE 323.28      2024-07-26            27.79        0.00   
19             19    PFE 342.65      2025-07-03            24.11        0.00   
20             20    PFE 311.02      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  \
18     2024-09-03           25.56       0.00 -721.15   -0.08      Long   
19     2025-08-08           23.76       0.00 -122.36   -0.01      Long   
20     2025-10-10           23.95       0.00 -691.38   -0.08      Long   

    Status  Position Id  
18  Closed           18  
19  Closed           19  
20    Open           20

In [95]:
pf.trades.records_readable.columns

Index(['Exit Trade Id', 'Column', 'Size', 'Entry Timestamp', 'Avg Entry Price',
       'Entry Fees', 'Exit Timestamp', 'Avg Exit Price', 'Exit Fees', 'PnL',
       'Return', 'Direction', 'Status', 'Position Id'],
      dtype='object')

For visualizing the trades, we can us the vbt-built-in plots. Since the built-in plots works only for one ticker, we need to apply it for each ticker separately (by adressing pf[ticker]).

In [96]:
# plotting trades of the individual tickers
n_cols = len(pf.wrapper.columns)

fig = make_subplots(rows=n_cols, cols=1,
    shared_xaxes=True, subplot_titles=[f"Trades for {col}" for col in pf.wrapper.columns],
    vertical_spacing=0.05
)

for i, col in enumerate(pf.wrapper.columns, start=1):
    trade_fig = pf[col].plot_trades()
    for trace in trade_fig.data:
        trace.showlegend = (i == 1)
        fig.add_trace(trace, row=i, col=1)

fig.update_layout( height=200 * n_cols, width=1000,
    title="Trades Overview", showlegend=True
)
fig.show()

### Outputs: Statistical Parameters

Calling `pf.stats()` returns aggregated statistics across all tickers in the portfolio. This aggregation is performed by simple averaging. While averaging is meaningful for some metrics (such as profits), it can produce less informative or even misleading results for others (for example, drawdowns).

In addition to the aggregated view, it is often useful to inspect the statistics of individual tickers. These are available via pf[ticker].stats().

In the code below, we first compute the aggregated statistics and rename the corresponding column. We then concatenate, ticker by ticker, the statistical metrics for each individual asset to obtain a comprehensive overview.

In [97]:
# stats per ticker and overall stats
stats = pf.stats()
stats.name='Portfolio (agg)'

for ticker in tickers:
    stats = pd.concat([stats, pf[ticker].stats()], axis=1)
display(stats)

/tmp/ipython-input-3630024687.py:2: UserWarning:

Object has multiple columns. Aggregating using <function mean at 0x786db8f75da0>. Pass column to select a single column/group.



Portfolio (agg)                  PFE  \
Start                       2022-01-03 00:00:00  2022-01-03 00:00:00   
End                         2025-10-10 00:00:00  2025-10-10 00:00:00   
Period                        947 days 00:00:00    947 days 00:00:00   
Start Value                           10,000.00            10,000.00   
End Value                              9,503.33             7,448.86   
Total Return [%]                          -4.97               -25.51   
Benchmark Return [%]                      -3.38               -47.21   
Max Gross Exposure [%]                   100.00               100.00   
Total Fees Paid                            0.00                 0.00   
Max Drawdown [%]                          30.33                30.16   
Max Drawdown Duration         586 days 00:00:00    707 days 00:00:00   
Total Trades                               5.25                    5   
Total Closed Trades                        4.75                    4   
Total Open Trades                          0.50                    1   
Open Trade PnL                           383.66              -691.38   
Win Rate [%]                              35.00                 0.00   
Best Trade [%]                             6.69                -1.48   
Worst Trade [%]                          -12.66                -8.03   
Avg Winning Trade [%]                      7.86                  NaN   
Avg Losing Trade [%]                      -9.06                -4.98   
Avg Winning Trade Duration     73 days 13:20:00                  NaT   
Avg Losing Trade Duration      25 days 00:00:00     28 days 18:00:00   
Profit Factor                              1.01                 0.00   
Expectancy                              -199.31              -464.94   
Sharpe Ratio                              -0.07                -0.97   
Calmar Ratio                               0.04                -0.36   
Omega Ratio                                0.96                 0.68   
Sortino Ratio                             -0.05                -1.26   

                                           GOOG                 MSFT  \
Start                       2022-01-03 00:00:00  2022-01-03 00:00:00   
End                         2025-10-10 00:00:00  2025-10-10 00:00:00   
Period                        947 days 00:00:00    947 days 00:00:00   
Start Value                           10,000.00            10,000.00   
End Value                             11,366.32            13,584.87   
Total Return [%]                          13.66                35.85   
Benchmark Return [%]                      64.82                57.46   
Max Gross Exposure [%]                   100.00               100.00   
Total Fees Paid                            0.00                 0.00   
Max Drawdown [%]                          22.57                18.42   
Max Drawdown Duration         499 days 00:00:00    339 days 00:00:00   
Total Trades                                  6                    5   
Total Closed Trades                           5                    5   
Total Open Trades                             1                    0   
Open Trade PnL                         2,226.01                 0.00   
Win Rate [%]                              60.00                60.00   
Best Trade [%]                             7.91                17.56   
Worst Trade [%]                          -16.30                -6.58   
Avg Winning Trade [%]                      5.46                15.34   
Avg Losing Trade [%]                     -11.56                -5.87   
Avg Winning Trade Duration     66 days 16:00:00     97 days 00:00:00   
Avg Losing Trade Duration      18 days 12:00:00     20 days 12:00:00   
Profit Factor                              0.61                 3.40   
Expectancy                              -171.94               716.97   
Sharpe Ratio                               0.34                 0.87   
Calmar Ratio                               0.22                 0.68   

In [98]:
stats.index

Index(['Start', 'End', 'Period', 'Start Value', 'End Value',
       'Total Return [%]', 'Benchmark Return [%]', 'Max Gross Exposure [%]',
       'Total Fees Paid', 'Max Drawdown [%]', 'Max Drawdown Duration',
       'Total Trades', 'Total Closed Trades', 'Total Open Trades',
       'Open Trade PnL', 'Win Rate [%]', 'Best Trade [%]', 'Worst Trade [%]',
       'Avg Winning Trade [%]', 'Avg Losing Trade [%]',
       'Avg Winning Trade Duration', 'Avg Losing Trade Duration',
       'Profit Factor', 'Expectancy', 'Sharpe Ratio', 'Calmar Ratio',
       'Omega Ratio', 'Sortino Ratio'],
      dtype='object')

In [99]:
stats.columns

Index(['Portfolio (agg)', 'PFE', 'GOOG', 'MSFT', 'MRNA'], dtype='object')

### Outputs: timelines of portfolio metrics
#### development of portfolio value over time

Now we want to analyse the timely-behaviour of portfolio metrics and parameters. We take the portfolio value as example. When calling `pf.value()` we get a dataframe with the development of the values (of each ticker) over time.

In [100]:
pf.value().tail(3)

Ticker          GOOG      MSFT     MRNA      PFE
Date                                            
2025-10-08 11,747.76 13,584.87 5,613.27 7,719.40
2025-10-09 11,592.22 13,584.87 5,613.27 7,587.13
2025-10-10 11,366.32 13,584.87 5,613.27 7,448.86

The timelines of the metrics can be visualized by the vbt-built-in methods:

In [101]:
pf.value().vbt.plot(
    width=800, height=300,
    title= 'Value of the portfolio members',
    ).show()

All the parameters introduced earlier are also accessible. For example, we can retrieve the final cumulative returns for each ticker as follows:

In [106]:
pf.cumulative_returns().iloc[-1].rename('final returns (EUR)')


Ticker
GOOG    0.14
MSFT    0.36
MRNA   -0.44
PFE    -0.26
Name: final returns (EUR), dtype: float64

Since `pf.value()`delivers a dataframe with the values of the multiple-tickers, the total portfolio value needs to be calculated separately by applying the .sum(axis=1)-method. WE can again use the vbt-built in plot function.

The final portfolio value is the last value of this time series. From this, we can also calculate the final profit (in EUR and in %).  

In [107]:
# calculating total portfolio value
total_value = pf.value().sum(axis=1)
total_value.vbt.plot(width=800, height=250, title= 'Total value of portfolio').show()

print(f'final total_value:  {total_value.iloc[-1]:,.2f} EUR')
print(f'final profit :      {total_value.iloc[-1]-total_cash:,.2f} EUR')
print(f'final profit %:     {(total_value.iloc[-1]-total_cash)/total_cash*100:,.2f} %')

final total_value:  38,013.32 EUR
final profit :      -1,986.68 EUR
final profit %:     -4.97 %


#### development of number of assets over time
Let's demonstrate the different options again, using the development of assets (= number of shares) over time.

In [20]:
# plotting development of assets of the individual tickers
n_cols = len(pf.wrapper.columns)

fig = make_subplots(rows=n_cols, cols=1,
    shared_xaxes=True, subplot_titles=[f"Assets for {col}" for col in pf.wrapper.columns],
    vertical_spacing=0.06
)

for i, col in enumerate(pf.wrapper.columns, start=1):
    trace_fig = pf[col].plot_assets()
    for trace in trace_fig.data:
        fig.add_trace(trace, row=i, col=1)

fig.update_layout( height=120 * n_cols, width=1000,
    title="Assets Overview", showlegend=False
)

In [21]:
# built in plots, calling once
pf.assets().vbt.plot(width=1000, height=250, title ='Number of assets').show()

#### development of cash over time
The development of cach over time can be show using the built in functions:

Note: in our portfolio, we form "cash-buckets" for each ticker in isolation. No cash-pooling/sharing is allowed. We will get back to this later.

In [22]:
pf.cash().vbt.plot(width=1000, height=250, title='Cash per portfolio memnber').show()

In [23]:
total_cash = pf.cash().sum(axis=1)
total_cash.vbt.plot(width=1200, height=150, title='Total cash').show()


#### development of drawdowns over time

By callling `pf.drawdown()` we get a dataframe, showing the individual drawdonws per ticker.

In [24]:
pf.drawdown().tail(3)

Ticker          GOOG      MRNA      MSFT       PFE
Date                                              
2025-10-08 -0.038317 -0.501634 -0.052492 -0.276236
2025-10-09 -0.051050 -0.501634 -0.052492 -0.288637
2025-10-10 -0.069542 -0.501634 -0.052492 -0.301601

these individual drawdowns can be visualized:

In [25]:
pf.drawdown().vbt.plot(width=1000, height=250, title='Individual drawdowns of portfolio members').show()


We can also generate a dashboard with the underwater-plots of all portfolio-members

In [108]:
# underwater plots of the individual tickers
n_cols = len(pf.wrapper.columns)

fig = make_subplots(
    rows=n_cols, cols=1,
    shared_xaxes=True,
    subplot_titles=[f"Underwater for {col}" for col in pf.wrapper.columns],
    vertical_spacing=0.05
)

for i, col in enumerate(pf.wrapper.columns, start=1):
    trace_fig = pf[col].plot_underwater()
    for trace in trace_fig.data:
        trace.showlegend = (i == 1)
        fig.add_trace(trace, row=i, col=1)

fig.update_layout(
    height=120 * n_cols, width=1000,
    title="Dashboard Underwater-Plots", showlegend=True
)

However, in a portfolio, we are primarily interested in the total drawdown. This cannot be calculated directly from the individual drawdowns of each ticker. Instead, we need to consider the total portfolio value—the sum of the values of all tickers.

From the time series of the total portfolio value, we can then compute the drawdown using the standard formulas, as follows:

In [109]:
# calculate total value and from that the drawdown
total_value = pf.value().sum(axis=1)
rolling_max = total_value.cummax()
drawdown = (total_value - rolling_max) / rolling_max

# plotting
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=drawdown.index, y=drawdown,
        mode='lines', name='Drawdown', fill='tozeroy', fillcolor='LightCoral',
        ),
    )
# finetuning
fig.update_layout(
    title='Portfolio Drawdown',
    xaxis_title='Date', yaxis_title='Drawdown', hovermode='x unified',
    width=900, height=300
)
fig.show()

### Timely Evolution of Portfolio Positions

When evaluating a strategy, it is often useful to visualize the positions of all portfolio members over time in a single dashboard. To facilitate this, we have created a function `plot_portfolio_positions(...)` (details are available in the GitHub repository).

This function is based on the sign of the net exposure, as explained in the previous sections, and provides an intuitive view of how positions evolve across all tickers throughout the trading period.

In [28]:
# plotting positions
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)


The methods presented so far provide suffcient tools to analyse the behaviour of the members of an multi-ticker-portfolio and of the aggregated parameters of the portfolio.

## Portfolio with individual allocation of initial cash

We generate now a portfolio-instance with the following features:
* multi-ticker-portfolio
* LongOnly
* distribution of total cash via weights into individual init_cash per ticker
* no cash_sharing

very important Note: The sequence of the ticker in tickers (e.g. for `yf.download`), does not match with the sequence of tickers in the portfolio-object, where the tickers are strictly ordered alphabetically. See the print out below:

In [29]:
display(f'sequence in tickers:      {tickers}')
display(f'sequence of cols in pf:   {pf.wrapper.columns.values.tolist()}')

"sequence in tickers:      ['PFE', 'GOOG', 'MSFT', 'MRNA']"

"sequence of cols in pf:   ['GOOG', 'MRNA', 'MSFT', 'PFE']"

Now we have to ensure that the weight is attributed to the right ticker and is correctly used in the portfolio object. To avoid any problems I used a mapping dictionary that contains the tickers and their weights. The dictionary is transformed to a PandasSeries, that is rearranged according to the sequence of tickers in portfolio. So in portfolio the correct weigths for the portfolio members are used.

In [111]:
# distribution of cash by weigths
weights = {
    'PFE': 0.4,
    'GOOG': 0.3,
    'MSFT': 0.2,
    'MRNA': 0.1
}
weights = pd.Series(weights)
weights = weights.reindex(close.columns)

total_cash = 10_000
init_cash_per_ticker = weights * total_cash

# generation of a baseline portfolio instance (multiple tickers)
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    #short_entries=short_entries,   # no short-entry
    #short_exits=short_exits,       # no short-exit
    init_cash=init_cash_per_ticker, # init_cash is distributed by weights
    freq='D'                        # daily evaluation of metrics
)

By plotting the absolute value development of the portfolio members, we can confirm that the weights have been assigned correctly.

If you choose not to use the methodology outlined above, it is essential to verify by other means that the weights are properly allocated. I strongly recommend always performing a double-check to avoid unintended allocation errors.


In [112]:
pf.value().vbt.plot(width=900, height=300, title='Value of portfolio members').show()

In [32]:
pf.value().sum(axis=1).vbt.plot(width=1000, height=250, title='Total value of portfolio').show()

## Portfolio with Cash-Pool

The next portfolio will have the following features:

* multi-ticker-portfolio
* LongOnly
* identical values for init_cash per ticker
* cash-pooling (=cash-sharing)

It is generated as follows:


In [127]:
# Total cash for the shared pool
total_cash = 10_000

# generation of a baseline portfolio instance (multiple tickers)
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    #short_entries=short_entries,   # no short-entry
    #short_exits=short_exits,       # no short-exit
    init_cash=total_cash,           # init_cash is distributed
    cash_sharing=True,              # one cash-pool for all tickers
    freq='D'                        # daily evaluation of metrics
)

Compared to the display of pf.value() for the same portfolio with `cash_sharing`= False, (that gives a dataframe with cash-values for each ticker) we see a different behaviour now. If pf.value() is displayed, we get only one column (named 'group').

The reason is straightforward. Since we pool the cash, there is no cash anymore attributed to a single ticker. Cash is available to all portfolio members.

Consequently metrics as pf.value() and pf.cash() shows for this set up only the aggregated values.

In [128]:
# printing and plotting
print('**** cash')
display(pf.cash().tail(3))
print()

print('**** value')
display(pf.value().tail(3))
print()

print('*** profit')
print(f'final profit :      {pf.value().iloc[-1]-total_cash :.3f}')
print()

**** cash


Date
2025-10-08   0.00
2025-10-09   0.00
2025-10-10   0.00
Name: group, dtype: float64


**** value


Date
2025-10-08   14,229.05
2025-10-09   14,040.65
2025-10-10   13,767.04
Name: group, dtype: float64


*** profit
final profit :      3767.037



We demonstrate now, how we can combine two different parameters by customizing the vbt-built-in plots. We will plot total value and cash in one plot. (if Long, cash is zero, if Flat, Value equal cash)

In [129]:
combined = pd.concat([
    pf.value().rename("Total Value"),
    pf.cash().rename("Cash")
], axis=1)

combined.vbt.plot(width=900, height=300,title='Total value and cash of the portfolio').show()

In contrast to cash, other portfolio parameters are still tracked per ticker. For example, the number of assets is always available individually for each ticker in the portfolio.

There are two ways to access these per-ticker parameters:

1. Using group_by=False: When calling a portfolio method (e.g., pf.assets()),

2. setting group_by=False returns a DataFrame with separate columns for each ticker, instead of aggregated values.

Accessing a specific ticker directly: You can also query an individual ticker by indexing the portfolio object, for example, pf.assets()[ticker]. This returns the time series for that particular ticker only.

Both approaches allow you to inspect ticker-level behavior even in a portfolio with cash pooling, while aggregated methods like pf.value() and pf.cash() reflect the combined portfolio-level view.

In [130]:
display(pf.assets().tail(3))
display(pf.asset_value(group_by=False).tail(3))

Ticker      GOOG  MSFT  MRNA  PFE
Date                             
2025-10-08 58.01  0.00  0.00 0.00
2025-10-09 58.01  0.00  0.00 0.00
2025-10-10 58.01  0.00  0.00 0.00

Ticker          GOOG  MSFT  MRNA  PFE
Date                                 
2025-10-08 14,229.05  0.00  0.00 0.00
2025-10-09 14,040.65  0.00  0.00 0.00
2025-10-10 13,767.04  0.00  0.00 0.00

In [131]:
# option 1
pf.asset_value(group_by=False).vbt.plot(
    width=900, height=250,
    title='Asset value of each portfolio member'
    ).show()


In [132]:
np.sign(pf.assets()).vbt.plot(
    width=1000, height=150,
    title='Position of each ticker',
    ).show()


In [126]:
# option 2
for ticker in pf.wrapper.columns:
    np.sign(pf.assets()[ticker]).vbt.plot(
        width=1000, height=100,
        title=f'Position Over Time – {ticker}',
        ).show()


In [134]:
# plotting positions
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

Of course we still have the list of trades with the key-trade-parameters:

In [41]:
trades = pf.trades.records_readable
display(trades.head(2))
display(trades.tail(2))

Exit Trade Id Column       Size Entry Timestamp  Avg Entry Price  \
0              0   GOOG  64.193888      2024-04-26       172.397003   
1              1   GOOG  56.465979      2024-10-30       175.258102   

   Entry Fees Exit Timestamp  Avg Exit Price  Exit Fees         PnL    Return  \
0         0.0     2024-07-26      167.614807        0.0 -306.987756 -0.027739   
1         0.0     2025-02-14      186.145325        0.0  614.757667  0.062121   

  Direction  Status  Position Id  
0      Long  Closed            0  
1      Long  Closed            1

Exit Trade Id Column        Size Entry Timestamp  Avg Entry Price  \
7              7   MSFT   24.276848      2025-05-02       432.958923   
8              8    PFE  387.191553      2024-07-26        27.789465   

   Entry Fees Exit Timestamp  Avg Exit Price  Exit Fees          PnL  \
7         0.0     2025-08-29      505.743439        0.0  1766.978625   
8         0.0     2024-09-03       25.558720        0.0  -863.725744   

     Return Direction  Status  Position Id  
7  0.168110      Long  Closed            7  
8 -0.080273      Long  Closed            8

We can also generate a table that shows per ticker:
* the total PnL of all trades of this ticker
* the number of trades of this ticker

In [42]:
results_multi_ticker(pf)

Total_PnL  Trade_Count
Column                        
GOOG     1,796.95            3
MRNA    -1,568.15            2
MSFT     4,401.96            3
PFE       -863.73            1


Total Profit Across All Tickers: 3,767.037
Total Number of Trades: 9


## Portfolio with Cash-Pool and order size-limitation

We will generate now the following portfolio-instance:
* multi-ticker-portfolio
* LongOnly
* cash-pooling,
* order size limits:
    * `size_type` = 'Percent', `size`= 0.3 -->  only 30% of available cash will be used
    * `min_size`= 5, minimum 5 assets per ticker to be traded

In [135]:
# Total cash-pool
total_cash = 10_000

# generation of portfolio-instance with cash-pool and oder-size-limitation
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    #short_entries=short_entries,   # no short-entry
    #short_exits=short_exits,       # no short-exit
    size_type='Percent',            # setting size type
    size=0.3,                       # use 30% of available cash
    min_size=5,                     # trade 5 assets min-
    init_cash=total_cash,           # value of the cash pool
    cash_sharing=True,              # cash-pool, all tickers share the same cash
    freq='D',                       # daily evaluation of metrics
)

In [136]:
trades = pf.trades.records_readable
display(trades.head(2))
display(trades.tail(2))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 18.03      2023-02-02           107.99        0.00   
1              1   GOOG 16.45      2023-05-11           116.03        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2023-02-23           90.39       0.00 -317.36   -0.16      Long  Closed   
1     2023-07-20          118.64       0.00   42.95    0.02      Long  Closed   

   Position Id  
0            0  
1            1

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
17             17    PFE 82.84      2025-07-03            24.11        0.00   
18             18    PFE 99.81      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  \
17     2025-08-08           23.76       0.00  -29.58   -0.01      Long   
18     2025-10-10           23.95       0.00 -221.88   -0.08      Long   

    Status  Position Id  
17  Closed           17  
18    Open           18

In [137]:
pf.value(group_by=False)

Ticker          GOOG      MSFT      MRNA       PFE
Date                                              
2022-01-03 10,000.00 10,000.00 10,000.00 10,000.00
2022-01-04 10,000.00 10,000.00 10,000.00 10,000.00
2022-01-05 10,000.00 10,000.00 10,000.00 10,000.00
2022-01-06 10,000.00 10,000.00 10,000.00 10,000.00
2022-01-07 10,000.00 10,000.00 10,000.00 10,000.00
...              ...       ...       ...       ...
2025-10-06 10,264.96 11,294.56  8,890.45  9,484.55
2025-10-07 10,242.51 11,294.56  8,890.45  9,469.12
2025-10-08 10,233.95 11,294.56  8,890.45  9,412.20
2025-10-09 10,217.29 11,294.56  8,890.45  9,369.75
2025-10-10 10,193.10 11,294.56  8,890.45  9,325.38

[947 rows x 4 columns]

In [138]:
pf.value(group_by=False).loc[:,'MRNA']

Date
2022-01-03   10,000.00
2022-01-04   10,000.00
2022-01-05   10,000.00
2022-01-06   10,000.00
2022-01-07   10,000.00
                ...   
2025-10-06    8,890.45
2025-10-07    8,890.45
2025-10-08    8,890.45
2025-10-09    8,890.45
2025-10-10    8,890.45
Name: MRNA, Length: 947, dtype: float64

In [139]:
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

In [48]:
results_multi_ticker(pf)

Total_PnL  Trade_Count
Column                        
GOOG       193.10            6
MRNA    -1,109.55            5
MSFT     1,294.56            3
PFE       -674.62            5


Total Profit Across All Tickers: -296.516
Total Number of Trades: 19


When plotting the total cash and the total value of the portfolio, we can clearly see the difference between a 30% usage of available cash and a 100% usage.

In [141]:
# cash and value development
combined = pd.concat([
    pf.value().rename("Total Value"),
    pf.cash().rename("Cash"),
    ], axis=1)

combined.vbt.plot(
    width=900, height=300,
    title="Portfolio Value and Cash over Time",
    ).show()


## Portfolio with Groups
Now we will generate the following portfolio:

* multi-ticker-portfolio
* LongOnly
* SMA/RSI Strategy
* grouping of tickers into two Groups (Tech and Pharma)
* cash equally distributed between the groups
* cash-pooling for each group, i.e. cash sharing between the tickers in a group

REMEMBER: Sequence of tickers in the Portfolio are different than in tickers! In order to avoid confusion, we will map each ticker with a group, using a dictionary (similar to the methodology, already introduced, when assigning weights).

We need to cluster the tickers, belonging to a certain group. In our case the first group is 'Tech', the member-tickers are put in the first section of the dictionary. The second group is 'Pharma', their tickers are put into the second section of the dictionary. Teh sequence of tickers in this dictionary (i.e. the keys) is now the leading sequence in the `Portfolio` object.

As a consequence we need to rearrange all inputs into the same sequnce (in the code called `new_order`)  

In [50]:
# Mapping tickers → group, allocating cash → group
mapping = {'GOOG': 'Tech', 'MSFT': 'Tech',
           'MRNA': 'Pharma', 'PFE': 'Pharma'}
groups = list(set(mapping.values()))

total_cash = 20_000
init_cash_per_group = total_cash/len(groups)

# reordering of relevant data to new_order (by groups)
new_order = list(mapping.keys())
close = close[new_order]
long_entries = long_entries[new_order]
long_exits = long_exits[new_order]

# CrossCheck
group_by = group_by = pd.Series(mapping)
print('Final group_by:     ', group_by.values.tolist())
print('sequence of columns:', close.columns.tolist())
print('groups:             ', groups)


Final group_by:      ['Tech', 'Tech', 'Pharma', 'Pharma']
sequence of columns: ['GOOG', 'MSFT', 'MRNA', 'PFE']
groups:              ['Tech', 'Pharma']


Now we generate the portfolio-instance with the features, mentioned above:

In [144]:
# generation of portfolio-instance with cash-pool and grouping
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    # short_entries=short_entries,  # no short entries
    # short_exits=short_exits,      # no short exits
    init_cash=init_cash_per_group,  # cash per group
    cash_sharing=True,              # group-wise-cash-pool, all group members share the same cash
    group_by=group_by,              # assign tickers to the groups
    freq='D',                       # daily evaluation of metrics
)

In [145]:
trades = pf.trades.records_readable
display(trades.head(2))
display(trades.tail(2))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 55.56      2023-02-02           107.99        0.00   
1              1   GOOG 38.24      2024-04-26           172.40        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2023-02-23           90.39       0.00 -977.76   -0.16      Long  Closed   
1     2024-07-26          167.61       0.00 -182.85   -0.03      Long  Closed   

   Position Id  
0            0  
1            1

Exit Trade Id Column   Size Entry Timestamp  Avg Entry Price  Entry Fees  \
12             12    PFE 106.69      2025-07-03            24.11        0.00   
13             13    PFE  96.84      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  \
12     2025-08-08           23.76       0.00  -38.10   -0.01      Long   
13     2025-10-10           23.95       0.00 -215.27   -0.08      Long   

    Status  Position Id  
12  Closed           12  
13    Open           13

If we use methods as pf.value(), we will only get aggregated values per group:

In [146]:
pf.value().tail(2)

Tech   Pharma
Date                        
2025-10-09 9,092.91 2,362.33
2025-10-10 8,915.72 2,319.27

In [147]:
pf.value().vbt.plot(
    width=900, height=250,
    title='Value of portfolio groups',
    ).show()

How to access the value of the single tickers? We can use the same methods, however, we have to set `group_by`= False.

In [148]:
pf.value(group_by=False).tail(2)

Ticker         GOOG     MSFT     MRNA      PFE
Date                                          
2025-10-09 6,379.13 8,713.79 2,797.18 3,565.15
2025-10-10 6,201.93 8,713.79 2,797.18 3,522.10

In [56]:
pf.value(group_by=False).vbt.plot(width=1000, height=250, title='Value of portfolio members').show()

We can also show the values of the groups and the total portfolio value in one plot by expanding the vbt-built-in plots.

In [149]:
fig = pf.value().vbt.plot(
    width=900, height=350,
    title='Value of portfolio (Total and per Group)')
fig.add_scatter(
    x=pf.value().index, y=pf.value().sum(axis=1),
    mode="lines", name="Total Value", line=dict(width=3))
fig.show()

Similar plot for cash.

In [58]:
# plotting of cash per ticker and total cash
fig = pf.cash(group_by=False).vbt.plot(width=1000, height=250, title = 'Cash (Total and per ticker)')

fig.add_scatter(x=pf.cash().index, y=pf.cash().sum(axis=1),
                mode="lines", name="Total Cash", line=dict(width=3))
fig.show()

For other parameters we can get the values per ticker directly (i.e. without group_by=False), even though we have grouped the ticker in the portfolio. Example is the parameter `assets` (showing the current number of asssets in a position).

In [59]:
pf.assets().vbt.plot(width=1000, height=250, title='Number of Assets').show()

We can also plot aggregated values per group.

In [60]:
pf['Tech'].assets().vbt.plot(width=1000, height=150, title='Number of Assets per Group Tech').show()
pf['Pharma'].assets().vbt.plot(width=1000, height=150, title='Number of Assets per Group Pharma').show()

In [61]:
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

In [62]:
results_multi_ticker(pf, init_cash_per_group)

Total_PnL  Trade_Count
Column                        
GOOG       336.55            4
MRNA    -3,007.05            4
MSFT     4,522.98            3
PFE     -1,194.76            3


Total Profit Across All Tickers: 657.712
Total Number of Trades: 14

*** total return per Group *****
Tech       0.486
Pharma    -0.420
Name: 2025-10-10 00:00:00, dtype: object


## Portfolio with Groups, different inital cash per group

Now we will implement:
* multi-ticker-portfolio
* LongOnly
* SMA/RSI Strategy
* grouping of tickers into two Groups (Tech and Pharma)
* cash sharing between the tickers in a group
* different inital cash per group

The portfolio instance is generated as follows:

In [63]:
# Mapping tickers → group, allocating cash → group
mapping = {'GOOG': 'Tech', 'MSFT': 'Tech',
           'MRNA': 'Pharma', 'PFE': 'Pharma'}
groups = list(set(mapping.values()))
group_by = pd.Series(mapping)

mapping_cash = {'Tech': 6000, 'Pharma': 4000}
init_cash_per_group = pd.Series(mapping_cash)

# Reorder close/entries/exits according to groups
new_order = list(mapping.keys())
close = close[new_order]
long_entries = long_entries[new_order]
long_exits = long_exits[new_order]

# Build portfolio with groups and differen inital cach per group
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    #short_entries=short_entries,   # no short entries
    #short_exits=short_exits,       # no short exits
    init_cash=init_cash_per_group,  # different cash per group
    cash_sharing=True,              # group-wise-cash-pool, all group members share the same cash
    group_by=group_by,              # assign tickers to the groups
    freq='D',                       # daily evaluation of metrics
)

In [64]:
fig = pf.value().vbt.plot(width=1000, height=250, title="Portfolio Value (Total and per Group)")
fig.add_scatter(x=pf.value().index, y=pf.value().sum(axis=1),
                mode="lines", name="Total Value", line=dict(width=3))
fig.show()

In [65]:
# development of positions over time
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

In [66]:
trades = pf.trades.records_readable
display(trades.head(2))
display(trades.tail(2))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 55.56      2023-02-02           107.99        0.00   
1              1   GOOG 38.24      2024-04-26           172.40        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2023-02-23           90.39       0.00 -977.76   -0.16      Long  Closed   
1     2024-07-26          167.61       0.00 -182.85   -0.03      Long  Closed   

   Position Id  
0            0  
1            1

Exit Trade Id Column   Size Entry Timestamp  Avg Entry Price  Entry Fees  \
12             12    PFE 106.69      2025-07-03            24.11        0.00   
13             13    PFE  96.84      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  \
12     2025-08-08           23.76       0.00  -38.10   -0.01      Long   
13     2025-10-10           23.95       0.00 -215.27   -0.08      Long   

    Status  Position Id  
12  Closed           12  
13    Open           13

In [67]:
# Results
results_multi_ticker(pf, init_cash_per_group)

Total_PnL  Trade_Count
Column                        
GOOG       201.93            4
MRNA    -1,202.82            4
MSFT     2,713.79            3
PFE       -477.90            3


Total Profit Across All Tickers: 1,234.991
Total Number of Trades: 14

*** total return per Group *****
Tech       0.486
Pharma    -0.420
dtype: object


## Portfolio with cash-pool per group, unsing 30% of availalable-cash per order

Now we will implement:
* multi-ticker-portfolio
* LongOnly
* SMA/RSI Strategy
* grouping of tickers into two Groups (Tec and Pharma)
* cash sharing between the tickers in a group
* different inital cash per group
* for each trade 30% of available cash is consumed

The portfolio instance is generated as follows:

In [68]:
# Mapping tickers → group, allocating cash → group
mapping = {'GOOG': 'Tech', 'MSFT': 'Tech',
           'MRNA': 'Pharma', 'PFE': 'Pharma'}
mapping_cash = {'Tech': 6000, 'Pharma': 4000}  # non uniform initial cash
group_by = pd.Series(mapping)
init_cash_per_group = pd.Series(mapping_cash)

# Reorder close/entries/exits according to groups
new_order = list(mapping.keys())
close = close[new_order]
long_entries = long_entries[new_order]
long_exits = long_exits[new_order]

# Build portfolio with groups and different inital cash per group
pf = vbt.Portfolio.from_signals(
    close=close,                    # price info (defines also the index of any timeline)
    entries=long_entries,           # series (boolean) of entry-signals
    exits=long_exits,               # series (boolean) of exit-signals
    # short_entries=short_entries,  # no short entries
    # short_exits=short_exits,      # no short exits
    size_type='Percent',            # use percent of available cash
    size=0.3,                       # 30%
    init_cash=init_cash_per_group,  # different initial-cash per group
    group_by=group_by,              # assign tickers to groups
    cash_sharing=True,              # group-wise-cash-pool, all group members share the same cash
    freq='D',                       # daily evaluation of metrics
)

In [69]:
trades = pf.trades.records_readable
display(trades.head(2))
display(trades.tail(2))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 16.67      2023-02-02           107.99        0.00   
1              1   GOOG 10.33      2023-05-11           116.03        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2023-02-23           90.39       0.00 -293.33   -0.16      Long  Closed   
1     2023-07-20          118.64       0.00   26.96    0.02      Long  Closed   

   Position Id  
0            0  
1            1

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
19             19    PFE 42.94      2025-07-03            24.11        0.00   
20             20    PFE 37.75      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees    PnL  Return Direction  Status  \
19     2025-08-08           23.76       0.00 -15.33   -0.01      Long  Closed   
20     2025-10-10           23.95       0.00 -83.91   -0.08      Long    Open   

    Position Id  
19           19  
20           20

In [155]:
# examples of parameters available on Group-Leel and Portfolio Level
fig = pf.value().vbt.plot(
    width=900, height=120,
    title='Portfolio Value (Total and per Group)')
fig.add_scatter(
    x=pf.value().index, y=pf.value().sum(axis=1),
    mode='lines', name='Total Value', line=dict(width=3))
fig.show()

pf.net_exposure().vbt.plot(
    width=900, height=120,
    title='Net Exposure (per Group)',
    ).show()

# examples of parameters available on single ticker levels
pf.assets().vbt.plot(
    width=900, height=120,
    title='Assets (per ticker)',
    ).show()
pf.asset_value(group_by=False).vbt.plot(
    width=900, height=120,
    title='Asset Value (per ticker)',
    ).show()

# example hot to aggregate parameters form single tickert so group
pf.asset_value().vbt.plot(
    width=900, height=120,
    title='Asset Value (per Group)',
    ).show()

In [71]:
pf.iloc[1].asset_value().vbt.plot(width=1000, height=150, title='Asset Value').show()

In [72]:
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

# plot cash over time
pf.cash().vbt.plot(width=950, height=150, title="Cash").show()

In [73]:
# Results
results_multi_ticker(pf, init_cash_per_group)

Total_PnL  Trade_Count
Column                        
GOOG       178.19            6
MRNA      -524.95            5
MSFT       663.26            5
PFE       -265.90            5


Total Profit Across All Tickers: 50.607
Total Number of Trades: 21

*** total return per Group *****
Tech       0.140
Pharma    -0.198
dtype: object


### Portfolios for Long/Short Strategies

Now let’s combine everything into a portfolio that supports both long and short trades. We implement a portfolio with the following features:

* Multi-ticker portfolio
* Long and short positions
* SMA/RSI strategy
* Grouping of tickers into multiple groups (e.g. Tech and Pharma)
* user-defined initial cash allocation per group
* Cash pooling within each group (cash sharing among tickers of the same group)
* No cash sharing between groups
* Support for long and short entry signals
* Support for long and short exit signals
* Group-aware handling of signals and portfolio metrics

We apply the methodology already discussed and extend it to include short positions. In addition to long_entries and long_exits, we now also use the short_entries and short_exits DataFrames.

As with the other inputs, these DataFrames must be rearranged to match the portfolio’s ticker order. In particular, their columns need to follow the new_order introduced earlier when grouping tickers. Ensuring consistent ordering across all inputs is essential for correct portfolio construction and signal interpretation.

In [160]:
# Mapping tickers → group, allocating cash → group
mapping = {'GOOG': 'Tech', 'MSFT': 'Tech',
           'MRNA': 'Pharma', 'PFE': 'Pharma'}
groups = list(set(mapping.values()))
group_by = pd.Series(mapping)

mapping_cash = {'Tech': 6000, 'Pharma': 4000}
init_cash_per_group = pd.Series(mapping_cash)

# Reorder close/entries/exits
new_order = list(mapping.keys())
close = close[new_order]
long_entries = long_entries[new_order]
long_exits = long_exits[new_order]
short_entries = short_entries[new_order]
short_exits = short_exits[new_order]

# generating Portfolio instance
pf = vbt.Portfolio.from_signals(
    close=close,
    entries=long_entries,
    exits=long_exits,
    short_entries=short_entries,
    short_exits=short_exits,
    accumulate=True,
    init_cash=init_cash_per_group,
    group_by=group_by,
    cash_sharing=True,
    freq='D'
)

Lets remember what we have discussed in the LongOnly Portfolio about conflicts. In a Long-Short-portfolio may have even more conflicts, since we may receive multiple signals from the Long and the Short side at one bar.

In a LongOnly system we need to define the behaviour, if a long_entry and a short_entry signal occures at the same bar. As alredy shown, we can define the behaviour by setting the parameter `upon_long_conflict`.

In a fully fledged Long-Short Portfolio we do have much more potential conflicts, that are regulated by setting different parameters.

We have as parameters:
* `upon_long_conflict` (see above)
* `upon_short_conflict` (regulates behaviour, if short_entry and short_exit signal occure on the same bar)
* `upon_dir_conflict`(regulates behaviour if long_entry and short_entry signal occures on the same bar)
* `upon_opposite_entry`(regulates behaviour if we are in a position, and an opposite entry signal occures)

Note about `upon_opposite_entry`: Assume we are Long. When in position we receive a short_entry signal (without a previous long_exit_signal). We have now a couple of options:
* Ignore (= Default): Do nothing
* Close: Close the current position
* CloseReduce: Close the current position, or reduce size (if `accumulation`=True)
* Reverse: Close the current positon and open the opposit position
* ReverseReduce: Close the current postion, or reduce size and built up opposite position (if `accumulation` = True)

With this we have a powerful arsenal of different behaviours, that can be used to define our portfolio.  




The Outputs are identical to our LongOnly-portfolio

In [161]:
trades = pf.trades.records_readable
display(trades.head(3))
display(trades.tail(3))

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   GOOG 52.56      2022-04-27           114.16        0.00   
1              1   GOOG 55.89      2023-02-02           107.99        0.00   
2              2   GOOG 38.46      2024-04-26           172.40        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2022-07-07          118.42       0.00 -223.55   -0.04     Short  Closed   
1     2023-02-23           90.39       0.00 -983.52   -0.16      Long  Closed   
2     2024-07-26          167.61       0.00 -183.93   -0.03      Long  Closed   

   Position Id  
0            0  
1            1  
2            2

Exit Trade Id Column   Size Entry Timestamp  Avg Entry Price  Entry Fees  \
21             21    PFE  79.04      2024-07-26            27.79        0.00   
22             22    PFE 136.04      2025-07-03            24.11        0.00   
23             23    PFE 123.48      2025-10-02            26.17        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  \
21     2024-09-03           25.56       0.00 -176.33   -0.08      Long   
22     2025-08-08           23.76       0.00  -48.58   -0.01      Long   
23     2025-10-10           23.95       0.00 -274.50   -0.08      Long   

    Status  Position Id  
21  Closed           21  
22  Closed           22  
23    Open           23

In [162]:
# Portfolio Value (Total and Groups)
fig = pf.value().vbt.plot(width=1000, height=250, title='Portfolio Value (Total and per Group)')
fig.add_scatter(x=pf.value().index, y=pf.value().sum(axis=1),
                mode="lines", name="Total Value", line=dict(width=3))
fig.show()


In [163]:
pf.value(group_by=False).vbt.plot(width=1000, height=250, title='Portfolio-member-values').show()

In [168]:
pf.assets().vbt.plot(
    width=900, height=250,
    title='number of assets',
    ).show()

In [169]:
pf.cash().vbt.plot(
    width=900, height=300,
    title='Cash per Group',
    ).show()

In [167]:
pos_ticker = np.sign(pf.assets())
plot_positions_stacked(pos_ticker)

In [81]:
# Results
results_multi_ticker(pf, init_cash_per_group)

Total_PnL  Trade_Count
Column                        
GOOG    -1,757.66            6
MRNA        74.64            7
MSFT     3,475.98            5
PFE     -1,117.22            6


Total Profit Across All Tickers: 675.735
Total Number of Trades: 24

*** total return per Group *****
Tech       0.286
Pharma    -0.261
dtype: object
